In [ ]:
# Load Image to Text model
from transformers import AutoProcessor, AutoModelForCausalLM
import requests

image_processor = AutoProcessor.from_pretrained("microsoft/git-base")
image_to_text_model = AutoModelForCausalLM.from_pretrained("microsoft/git-base")

In [ ]:
# Load Translation model
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

tokenizer = AutoTokenizer.from_pretrained("google-t5/t5-small")
model = AutoModelForSeq2SeqLM.from_pretrained("google-t5/t5-small")

In [ ]:
def generate_caption(image):
  pixel_values = image_processor(images=image, return_tensors="pt").pixel_values
  generated_ids = image_to_text_model.generate(pixel_values=pixel_values, max_length=200)
  generated_caption = image_processor.batch_decode(generated_ids, skip_special_tokens=True)[0]

  return generated_caption

In [ ]:
def translate(text):
  inputs = tokenizer(text, return_tensors='pt')
  input_ids = inputs.input_ids
  attention_mask = inputs.attention_mask

  try:
    input_ids = input_ids.to('cuda')
    attention_mask = attention_mask.to('cuda')
    model = translation_model.to("cuda")
  except:
    print('No NVidia GPU, model performance may not be as good')
    model = translation_model

  output = model.generate(input_ids, attention_mask=attention_mask, forced_bos_token_id=tokenizer.lang_code_to_id['pt_XX'])
  translated = tokenizer.decode(output[0], skip_special_tokens=True)

  return translated

In [ ]:
# Carregamento de imagens locais
import sys
import cv2
from PIL import Image

img_url = 'http://images.cocodataset.org/val2017/000000039769.jpg'
# img_url = 'https://farm4.staticflickr.com/3733/9000662079_ce3599d0d8_z.jpg'
# img_url = 'https://farm4.staticflickr.com/3088/5793281956_2a15b2559c_z.jpg'
# img_url = 'https://farm5.staticflickr.com/4073/4816939054_844feb0078_z.jpg'

image = Image.open(requests.get(img_url, stream=True).raw)

In [ ]:
caption = generate_caption(image)

print(caption)

In [ ]:
translated_caption = translate(caption)

print(translated_caption)